In [300]:
import firedecomp.plot.simulations as plot_sim

import json
import plotly
import plotly.graph_objs as go
import plotly.offline
plotly.offline.init_notebook_mode()
import plotly.express as px
import qgrid

# Introduction

This notebook summarize the main results obtained in the simulations done.

## Install extensions

Follow link instructions:
http://tljh.jupyter.org/en/latest/howto/admin/enable-extensions.html

## Install qgrid

To enable qgrid in jupyter notebook follow the instructions described in:
https://github.com/quantopian/qgrid

**Installing with pip**:

```python
pip install qgrid
jupyter nbextension enable --py --sys-prefix qgrid

# only required if you have not enabled the ipywidgets nbextension yet
jupyter nbextension enable --py --sys-prefix widgetsnbextension
```

**Installing with conda**:
```python
# only required if you have not added conda-forge to your channels yet
conda config --add channels conda-forge

conda install qgrid
```

## Install Orca (export plotly figure to file)

For orca installation type:
```
conda install -c plotly plotly-orca
```

Alternatively, see other installation methods in the orca project README at
https://github.com/plotly/orca

If you have installed orca, then for some reason plotly.py was unable to
locate it. In this case, set the `plotly.io.orca.config.executable`
property to the full path of your orca executable. For example:
```python
plotly.io.orca.config.executable = "/path/to/orca"
```
And save the configuration:
```python
plotly.io.orca.config.save()
```

In [301]:
plotly.io.orca.config.executable = "/home/jorge/.nvm/versions/node/v13.12.0/bin/orca"
plotly.io.orca.config.save()

## Install Node (necessary for Orca)

In Linux to install nodejs type:
```
sudo apt-get install nodejs
```

# General Information

Use desired colors:

In [302]:
fig = px.colors.qualitative.swatches()
fig.show()

Information used in scatters:

In [303]:
# Black and white
rename = {
    'original': 'OP',
    'AL': 'AL', # Augmented Lagrange
    'gcg_scip': 'BP', # Branch and Price
    'benders': 'BD',
    'fix_work': 'FA', # Fix activity 
}

lines={
    'original': {
        'color': 'rgb(0,0,0)',
        'dash': 'dash'
    },
    'AL': {
        'color': 'rgb(225,225,225)',
    },
    'gcg_scip': {
        'color': 'rgb(0,0,0)',
    },
    'benders': {
        'color': 'rgb(75,75,75)',
    },
    'fix_work': {
        'color': 'rgb(150,150,150)',
    },
}

# Color
pallete = px.colors.qualitative.Set1
lines={
    'original': {
        'color': pallete[0],
        'dash': 'dash'
    },
    'AL': {
        'color': pallete[4],
    },
    'gcg_scip': {
        'color': pallete[3],
    },
    'benders': {
        'color': pallete[2],
    },
    'fix_work': {
        'color': pallete[1],
    },
}


filter_best = [{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}]

With the filter we are only considering feasible cases to compute the best performance.

### Layout

In [304]:
margin = {
    'l': 40,
    'r': 10,
    'b': 80,
    't': 10
}

margin_boxplot = {
    'l': 80,
    'r': 10,
    'b': 100,
    't': 10
}

font={"size": 20}

#### Normal Layout

In [305]:
layout = None
layout_boxplot = {
    'margin': margin_boxplot, 
    'boxmode': 'group',
    'font': font,
}

#### Paper Single Figure Layout

In [306]:
layout_paper_single = {
    'autosize': False,
    'width': 600,
    'height': 400,
    'margin': margin,
    'font': font,
}

layout_boxplot_paper_single = {
    'autosize': False,
    'width': 600,
    'height': 400,
    'margin': margin_boxplot,
    'boxmode': 'group',
    'font': font,
}

#### Paper Double Figure Layout

In [307]:
layout_paper_double_legend = {
    'autosize': False,
    'width': 600,
    'height': 400,
    'margin': margin,
    'font': font,
}

layout_paper_double = {
    'autosize': False,
    'width': 500,
    'height': 400,
    'margin': margin,
    'showlegend': False,
    'font': font,
}

layout_boxplot_paper_double_legend = {
    'autosize': False,
    'width': 600,
    'height': 400,
    'margin': margin_boxplot, 
    'boxmode': 'group',
    'font': font,
}

layout_boxplot_paper_double = {
    'autosize': False,
    'width': 500,
    'height': 400,
    'margin': margin_boxplot, 
    'boxmode': 'group',
    'showlegend': False,
    'font': font,
}

#### Paper Zoom Figure Layout

In [308]:
layout_boxplot_paper_zoom = {
    'autosize': False,
    'width': 500,
    'height': 200,
    'margin': margin_boxplot, 
    'boxmode': 'group',
    'showlegend': False,
    'font': font,
}

# Small Cases

In [309]:
df = plot_sim.read_csvs(folder="Small_cases", file="solution.csv")

Small cases information:

In [310]:
qgrid.show_grid(df)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

Number of infeasible solutions per method:

In [311]:
for m in set(df['mode']):
    total = sum(df['mode'] == m)
    feasible = sum(df[df['mode'] == m]['constrvio'] < 0.0001)
    print(f"Mode {m}:")
    print(f"- Total: {total}")
    print(f"- Infeasible: {total - feasible}")
    print(f"- Percentaje: {(total - feasible)/total}")

Mode original:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875
Mode gcg_scip:
- Total: 1600
- Infeasible: 165
- Percentaje: 0.103125
Mode AL:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875
Mode fix_work:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875
Mode benders:
- Total: 1600
- Infeasible: 35
- Percentaje: 0.021875


## Group by instances

In [312]:
groupby = ['num_brigades', 'num_aircraft', 'num_machines',
                   'num_periods', 'seed']

sense_instances = df.groupby(groupby)
obj_fun = sense_instances['obj_fun'].min()
df = df.set_index(groupby).reset_index()

In [313]:
grid_options = plot_sim.get_qgrid_options()

In [314]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defa…

## Statistics

Get statistical information:

In [315]:
filter_df = plot_sim.get_best(df, filter_best=filter_best)
filter_df["num_resources"] = filter_df["num_brigades"] + filter_df["num_aircraft"] + filter_df["num_machines"]

In [316]:
stats = filter_df.groupby(['mode']).agg({
    'rel_elapsed_time': ['min', 'mean', 'median', 'max', 'std', 'count'],
    'rel_obj_fun': ['min', 'mean', 'median', 'max', 'std', 'count']
})

### Objective function (relative)

In [317]:
stats.loc[:,('rel_obj_fun','solved (%)')] = 100*stats['rel_obj_fun']['count']/len(filter_df[filter_df['mode']=="fix_work"])
rel_obj_fun_stats = stats['rel_obj_fun'].loc[:,("min", "mean", "median", "max", "std", "solved (%)")]
rel_obj_fun_stats

min      mean    median       max           std  solved (%)
mode                                                                 
AL        1.0  1.000721  1.000138  1.100093  7.124404e-03  100.000000
benders   1.0  1.000000  1.000000  1.000017  4.258439e-07  100.000000
fix_work  1.0  1.000000  1.000000  1.000017  4.263711e-07  100.000000
gcg_scip  1.0  1.070885  1.000177  1.857783  1.256582e-01   91.693291
original  1.0  1.000000  1.000000  1.000017  4.257315e-07  100.000000

In [318]:
# print(rel_obj_fun_stats.to_latex())

### Elapsed time (relative)

In [319]:
stats.loc[:,('rel_elapsed_time','solved (%)')] = 100*stats['rel_elapsed_time']['count']/len(filter_df[filter_df['mode']=="fix_work"])
rel_time_stats = stats['rel_elapsed_time'].loc[:,("min", "mean", "median", "max", "std", "solved (%)")]
rel_time_stats

min        mean      median          max         std  \
mode                                                                    
AL        161.168241  862.199610  811.287095  1719.746020  329.811687   
benders     3.052936    5.848005    5.391967    46.755790    2.732765   
fix_work    1.000000    1.012652    1.000000     4.372481    0.094572   
gcg_scip    4.237596  732.427410  431.506469  3164.330002  695.192498   
original    1.000000    1.797177    1.432915     8.569794    0.988304   

          solved (%)  
mode                  
AL        100.000000  
benders   100.000000  
fix_work  100.000000  
gcg_scip   91.693291  
original  100.000000

In [320]:
# print(rel_time_stats.to_latex())

## Performance Profiles

### Relative objective function

In [321]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_obj_fun', 
    rename=rename,
    lines=lines,
    filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}],
    xaxis={'title': "Relative Objective Function"},
    npoints=500,
    image_filename="small_perf_obj.png",
    layout=layout_paper_double
)

Same plot but with zoom in x axis:

In [322]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_obj_fun', 
    rename=rename,
    lines=lines,
    filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}],
    xaxis={'title': "Relative Objective Function"},
    npoints=500,
    max_x=1.01,
    image_filename="small_perf_obj_zoom.png",
    layout=layout_paper_double_legend
)

### Relative Elapsed Time

In [323]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_elapsed_time',
    rename=rename,
    lines=lines,
    filter_best=filter_best,
    xaxis={'title': "Relative Compuational Time"},
    npoints=500,
    image_filename="small_perf_time.png",
    layout=layout_paper_double
)

Same plot but with zoom in x axis:

In [324]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_elapsed_time', 
    rename=rename,
    lines=lines,
    filter_best=filter_best,
    xaxis={'title': "Relative Compuational Time"},
    npoints=500,
    max_x=20,
    image_filename="small_perf_time_zoom.png",
    layout=layout_paper_double_legend
)

## Boxplots

In [325]:
modes = ['original', 'AL', 'gcg_scip', 'benders', 'fix_work']

colors = {k: v['color'] for k, v in lines.items()}

### Objective function (relative)

In [326]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="rel_obj_fun", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', "num_periods"],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Relative Objective Function'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="small_box_rel_obj.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)

### Elapsed time (relative)

In [327]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="rel_elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Relative Compuational Time'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="small_box_rel_time.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)


In [328]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="rel_elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_zoom,
    yaxis={"range": [0, 45]},
    image_filename="small_box_rel_time_zoom.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)

### Elapsed time (absolute)

In [329]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Compuational Time'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="small_box_time.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)


In [330]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_zoom,
    yaxis={"range": [0, 20]},
    image_filename="small_box_time_zoom.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)

---------------------------------------------

# Huge Cases

In [331]:
df = plot_sim.read_csvs(folder="Huge_cases", file="solution.csv")

In [332]:
grid_options = plot_sim.get_qgrid_options()

In [333]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defa…

Number of infeasible solutions per method:

In [334]:
for m in set(df['mode']):
    total = sum(df['mode'] == m)
    feasible = sum(df[df['mode'] == m]['constrvio'] < 0.0001)
    print(f"Mode {m}:")
    print(f"- Total: {total}")
    print(f"- Infeasible: {total - feasible}")
    print(f"- Percentaje: {(total - feasible)/total}")

Mode original:
- Total: 4800
- Infeasible: 128
- Percentaje: 0.02666666666666667
Mode fix_work:
- Total: 4800
- Infeasible: 2
- Percentaje: 0.0004166666666666667


## Group by instances

In [335]:
groupby = ['num_brigades', 'num_aircraft', 'num_machines',
                   'num_periods', 'seed']

sense_instances = df.groupby(groupby)
obj_fun = sense_instances['obj_fun'].min()
df = df.set_index(groupby).reset_index()

In [336]:
qgrid.show_grid(df, grid_options=grid_options)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': False, 'defa…

## Statistics

Get statistical information:

In [337]:
filter_df = plot_sim.get_best(df, filter_best=filter_best)
filter_df["num_resources"] = filter_df["num_brigades"] + filter_df["num_aircraft"] + filter_df["num_machines"]

In [338]:
stats = filter_df.groupby(['mode']).agg({
    'rel_elapsed_time': ['min', 'mean', 'median', 'max', 'std', 'count'],
    'rel_obj_fun': ['min', 'mean', 'median', 'max', 'std', 'count']
})

### Objective function (relative)

In [339]:
stats.loc[:,('rel_obj_fun','solved (%)')] = 100*stats['rel_obj_fun']['count']/len(filter_df[filter_df['mode']=="fix_work"])
rel_obj_fun_stats = stats['rel_obj_fun'].loc[:,("min", "mean", "median", "max", "std", "solved (%)")]
rel_obj_fun_stats

min      mean  median       max       std  solved (%)
mode                                                           
fix_work  1.0  1.000000     1.0  1.000161  0.000003  100.000000
original  1.0  1.014159     1.0  8.911114  0.209779   97.373906

In [340]:
# print(rel_obj_fun_stats.to_latex())

### Elapsed time (relative)

In [341]:
stats.loc[:,('rel_elapsed_time','solved (%)')] = 100*stats['rel_elapsed_time']['count']/len(filter_df[filter_df['mode']=="fix_work"])
rel_time_stats = stats['rel_elapsed_time'].loc[:,("min", "mean", "median", "max", "std", "solved (%)")]
rel_time_stats

min      mean    median        max       std  solved (%)
mode                                                              
fix_work  1.0  1.252280  1.000000  91.394141  2.180038  100.000000
original  1.0  4.023912  2.489009  65.969051  4.068093   97.373906

In [342]:
# print(rel_time_stats.to_latex())

## Performance profile

### Relative Elapsed Time

In [343]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_elapsed_time', 
    rename=rename,
    lines=lines,
    filter_best=filter_best,
    xaxis={'title': "Relative Compuational Time"},
    image_filename="huge_perf_time.png",
    layout=layout_paper_double
)

In [344]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_elapsed_time', 
    rename=rename,
    lines=lines,
    filter_best=filter_best,
    max_x=10,
    xaxis={'title': "Relative Compuational Time"},
    image_filename="huge_perf_time_zoom.png",
    layout=layout_paper_double_legend
)

### Relative objective function

In [345]:
plot_sim.performance_profile_graph(
    df, 
    x='rel_obj_fun', 
    rename=rename,
    lines=lines,
    filter_best=[{'column': 'constrvio', 'operator': 'lt', 'value': 0.0001}],
    xaxis={'title': "Relative Objective Function"},
    image_filename="huge_perf_obj.png",
    layout=layout_paper_single
)

## Boxplots

In [346]:
modes = ['original', 'fix_work']

colors = {k: v['color'] for k, v in lines.items()}

### Objective function (relative)

In [347]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="rel_obj_fun", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', "num_periods"],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Relative Objective Function'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="huge_box_rel_obj.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)

### Elapsed time (relative)

In [348]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="rel_elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Relative Compuational Time'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="huge_box_rel_time.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)


### Elapsed time (absolute)

In [349]:
plot_sim.sim_boxplot(
    filter_df.sort_values(["num_resources", "num_periods"]), 
    y="elapsed_time", 
    rename=rename,
    modes=modes, 
    columns=['num_resources', 'num_periods'],
    colors=lines,
    layout=layout_boxplot_paper_single,
    yaxis={'title': 'Compuational Time'},
    xaxis={'title': 'Resources | Periods'},
    image_filename="huge_box_time.png",
    image_height=600,
    image_width=1000,
    sep=" | "
)
